# Optimize Initial Conditions
## Yabox

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from yabox import DE

# Load solver

In [2]:
LoadBH=True
if LoadBH:
    import LearnerICRayNoLoadBH as L 
else:
    import LearnerICRayNoLoad as L 

# Load Data

In [3]:
def load_confirmed(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Data for States

In [4]:
dfparam = pd.read_csv("data/param.csv")
dfparam

state  start-date  prediction-range         s0  e0  a0   i0   r0   d0  \
0    SP  2020-03-15               200  8000000.0   0   0  800  300  250   
1    ES  2020-04-01               200   475000.0   0   0   50  250   50   
2    MG  2020-04-01               200  1100000.0   0   0  200  250   40   
3    RJ  2020-03-20               200   700000.0   0   0  800  250   50   
4    CE  2020-03-20               200   800000.0   0   0  800  250   50   
5    PE  2020-03-20               200   700000.0   0   0  800  250  100   
6    AM  2020-03-20               200   700000.0   0   0  800  250  100   

   START  RATIO  WCASES  WREC  
0    100   0.15    0.55  0.01  
1    100   0.15    0.65  0.01  
2    100   0.15    0.55  0.01  
3    100   0.15    0.50  0.01  
4    100   0.15    0.50  0.01  
5    100   0.15    0.50  0.01  
6    100   0.15    0.50  0.01

In [5]:
df = pd.read_csv("data/dados_total_estados.csv")
df

index        date state   city place_type  confirmed  deaths  \
0          0  2020-06-06    SE  TOTAL      state       8972     208   
1          1  2020-06-05    SE  TOTAL      state       8577     198   
2          2  2020-06-04    SE  TOTAL      state       8200     186   
3          3  2020-06-03    SE  TOTAL      state       7989     180   
4          4  2020-06-02    SE  TOTAL      state       7555     172   
...      ...         ...   ...    ...        ...        ...     ...   
2244  158210  2020-03-11    BA  TOTAL      state          3       0   
2245  158211  2020-03-10    BA  TOTAL      state          2       0   
2246  158212  2020-03-09    BA  TOTAL      state          2       0   
2247  158213  2020-03-07    BA  TOTAL      state          2       0   
2248  158214  2020-03-06    BA  TOTAL      state          1       0   

      order_for_place  is_last      popEst  city_ibge_code  \
0                  74     True   2298696.0            28.0   
1                  73    False   2298696.0            28.0   
2                  72    False   2298696.0            28.0   
3                  71    False   2298696.0            28.0   
4                  70    False   2298696.0            28.0   
...               ...      ...         ...             ...   
2244                5    False  14873064.0            29.0   
2245                4    False  14873064.0            29.0   
2246                3    False  14873064.0            29.0   
2247                2    False  14873064.0            29.0   
2248                1    False  14873064.0            29.0   

      confirmed_per_100k_inhabitants  death_rate  
0                          390.30824      0.0232  
1                          373.12459      0.0231  
2                          356.72399      0.0227  
3                          347.54487      0.0225  
4                          328.66460      0.0228  
...                              ...         ...  
2244                         0.02017      0.0000  
2245                         0.01345      0.0000  
2246                         0.01345      0.0000  
2247                         0.01345      0.0000  
2248                         0.00672      0.0000  

[2249 rows x 13 columns]

# Functions for Optimization

In [6]:
from scipy.integrate import odeint
import os
import sys
import io
import ray
import gc

def create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(state,date)
        data = load_confirmed(state,date)*(1-ratio)-dead
        
        cleanRecovered=False
        s0, deltaDate, i0, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=+int(deltaDate))
                    
        f=L.Learner.remote(state, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead, point,f         

        gc.collect()

        return result
    return fobjective

In [7]:
@ray.remote(memory=50 * 1024 * 1024, max_calls=7)
def opt(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):

    bounds=[(0.8*s0,1.2*s0),(-10,10),(0.8*i0,1.2*i0),\
              (0.3,0.7),(.001,.05)]
    maxiterations=300
    f=create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version)
    de = DE(f, bounds, maxiters=maxiterations)
    for step in de.geniterator():
        try:
            idx = step.best_idx
            norm_vector = step.population[idx]
            best_params = de.denormalize([norm_vector])
            del norm_vector, idx
        except:
            print("error in function evaluation")
    p=best_params[0]
    del f, bounds, data, dead
    
    return p

# Main Code

In [8]:
states=['SP','ES','MG','RJ','PE','CE','AM']
# states=['MG','RJ','PE','CE','AM']
allStates=True
version="102"
ray.shutdown()
GB=1024*1024*1024
MB=1024*1024
import cupy
ray.init(object_store_memory=500*MB,memory=2*GB,lru_evict=True,\
         driver_object_store_memory=50*MB,num_gpus=12,num_cpus=7)
gc.enable()

optimal=[]
if allStates:
    for state in states:
        #remove previous history file
        strFile='./results/history_'+state+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('state == "{}"'.format(state)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
        optimal.append(opt.remote(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version))        
else:
    state = "ES" 
    #remove previous history file
    strFile='./results/history_'+state+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    start_date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    optimal.append(opt.remote(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version))        

2020-06-15 18:06:43,305	INFO resource_spec.py:212 -- Starting Ray with 1.95 GiB memory available for workers and up to 0.49 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-06-15 18:06:43,725	INFO services.py:1170 -- View the Ray dashboard at localhost:8267


In [ ]:
optimal=ray.get(optimal)


(pid=144015) basinhopping step 0: f 1.59092e+08
(pid=144012) basinhopping step 0: f 2.07894e+08
(pid=144015) basinhopping step 1: f 1.57766e+08 trial_f 1.57766e+08 accepted 1  lowest_f 1.57766e+08
(pid=144015) found new global minimum on step 1 with function value 1.57766e+08
(pid=143906) basinhopping step 0: f -2.00209e+11
(pid=144015) basinhopping step 2: f 1.57766e+08 trial_f 7.30429e+08 accepted 0  lowest_f 1.57766e+08
(pid=144013) basinhopping step 0: f -1.12692e+10
(pid=143929) basinhopping step 0: f -6.67904e+13
(pid=144012) basinhopping step 1: f 2.07894e+08 trial_f 2.81073e+08 accepted 0  lowest_f 2.07894e+08
(pid=143923) basinhopping step 0: f -4.49176e+11
(pid=143929) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=143929)   warnings.warn(warning_msg, ODEintWarning)
(pid=144015) basinhopping step 3: f 1.41218

(pid=143929) basinhopping step 7: f -6.67904e+13 trial_f 9.07134e+09 accepted 0  lowest_f -6.67904e+13
(pid=143929) warning: basinhopping: local minimization failure
(pid=143929) basinhopping step 8: f -6.67904e+13 trial_f 1.17447e+14 accepted 0  lowest_f -6.67904e+13
(pid=144012) basinhopping step 8: f -3.37542e+11 trial_f 2.36234e+09 accepted 0  lowest_f -3.37542e+11
(pid=143929) basinhopping step 9: f -6.67904e+13 trial_f 2.14052e+11 accepted 0  lowest_f -6.67904e+13
(pid=144013) basinhopping step 10: f -5.75228e+11 trial_f 1.40947e+08 accepted 0  lowest_f -5.75228e+11
(pid=144045) basinhopping step 2: f -1.84845e+11 trial_f -1.84845e+11 accepted 1  lowest_f -1.84845e+11
(pid=144045) found new global minimum on step 2 with function value -1.84845e+11
(pid=143923) basinhopping step 5: f -1.15414e+12 trial_f -1.15414e+12 accepted 1  lowest_f -1.15414e+12
(pid=143923) found new global minimum on step 5 with function value -1.15414e+12
(pid=144045) basinhopping step 3: f -1.84845e+11 tr

(pid=1841) basinhopping step 1: f 1.57627e+08 trial_f 6.7388e+08 accepted 0  lowest_f 1.57627e+08
(pid=1840) basinhopping step 2: f -2.74543e+11 trial_f -2.74543e+11 accepted 1  lowest_f -2.74543e+11
(pid=1840) found new global minimum on step 2 with function value -2.74543e+11
(pid=144019) warning: basinhopping: local minimization failure
(pid=144019) basinhopping step 5: f -6.64652e+11 trial_f 1.55068e+08 accepted 0  lowest_f -6.64652e+11
(pid=1840) basinhopping step 3: f -2.74543e+11 trial_f 3.53699e+08 accepted 0  lowest_f -2.74543e+11
(pid=144060) basinhopping step 2: f -9.79904e+13 trial_f -9.79904e+13 accepted 1  lowest_f -9.79904e+13
(pid=144060) found new global minimum on step 2 with function value -9.79904e+13
(pid=144060) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=144060)   warnings.warn(warning_msg, OD

(pid=6177) basinhopping step 5: f -1.65698e+11 trial_f -1.65632e+11 accepted 0  lowest_f -1.65698e+11
(pid=144060) basinhopping step 5: f -9.79904e+13 trial_f -3.32036e+13 accepted 0  lowest_f -9.79904e+13
(pid=7098) basinhopping step 0: f -5.30598e+11
(pid=144020) basinhopping step 10: f -6.1248e+11 trial_f 1.38128e+08 accepted 0  lowest_f -6.1248e+11
(pid=6177) basinhopping step 6: f -1.65698e+11 trial_f 1.58553e+08 accepted 0  lowest_f -1.65698e+11
(pid=6177) basinhopping step 7: f -1.65698e+11 trial_f 1.81257e+08 accepted 0  lowest_f -1.65698e+11
(pid=7098) basinhopping step 1: f -5.30598e+11 trial_f 6.13144e+08 accepted 0  lowest_f -5.30598e+11
(pid=7097) basinhopping step 4: f -1.02142e+11 trial_f -1.02141e+11 accepted 0  lowest_f -1.02142e+11
(pid=7097) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=7097)   warn

(pid=7098) basinhopping step 10: f -5.30598e+11 trial_f -2.26136e+09 accepted 0  lowest_f -5.30598e+11
(pid=13699) basinhopping step 0: f -3.20666e+11
(pid=13710) basinhopping step 0: f 1.73814e+08
(pid=13710) basinhopping step 1: f 1.70997e+08 trial_f 1.70997e+08 accepted 1  lowest_f 1.70997e+08
(pid=13710) found new global minimum on step 1 with function value 1.70997e+08
(pid=144060) basinhopping step 9: f -9.79904e+13 trial_f 3.15237e+10 accepted 0  lowest_f -9.79904e+13
(pid=10850) warning: basinhopping: local minimization failure
(pid=10850) basinhopping step 7: f -1.80076e+11 trial_f -3.04426e+09 accepted 0  lowest_f -1.80076e+11
(pid=13699) basinhopping step 1: f -3.20666e+11 trial_f 8.20125e+07 accepted 0  lowest_f -3.20666e+11
(pid=13710) basinhopping step 2: f 2.5253e+07 trial_f 2.5253e+07 accepted 1  lowest_f 2.5253e+07
(pid=13710) found new global minimum on step 2 with function value 2.5253e+07
(pid=9175) warning: basinhopping: local minimization failure
(pid=9175) basinh

...

(pid=75277) basinhopping step 10: f -2.64092e+11 trial_f 1.47425e+09 accepted 0  lowest_f -2.64092e+11
(pid=75495) basinhopping step 5: f -3.8755e+11 trial_f -3.8755e+11 accepted 1  lowest_f -3.8755e+11
(pid=75495) found new global minimum on step 5 with function value -3.8755e+11
(pid=75495) basinhopping step 6: f -3.8755e+11 trial_f 1.9156e+08 accepted 0  lowest_f -3.8755e+11
(pid=75932) basinhopping step 2: f 1.22118e+08 trial_f 6.25303e+08 accepted 0  lowest_f 1.22118e+08
(pid=75931) basinhopping step 0: f -7.42311e+10
(pid=75931) basinhopping step 1: f -7.42311e+10 trial_f 5.43114e+10 accepted 0  lowest_f -7.42311e+10
(pid=75186) basinhopping step 9: f -8.68184e+13 trial_f 5.5778e+10 accepted 0  lowest_f -8.68184e+13
(pid=75902) warning: basinhopping: local minimization failure
(pid=75902) basinhopping step 3: f 1.64392e+08 trial_f 1.90682e+08 accepted 0  lowest_f 1.64392e+08
(pid=75902) basinhopping step 4: f 1.64392e+08 trial_f 1.67582e+08 accepted 0  lowest_f 1.64392e+08
(pid=7

(pid=75931) warning: basinhopping: local minimization failure
(pid=75931) basinhopping step 9: f -2.08395e+11 trial_f 3.69851e+10 accepted 0  lowest_f -2.08395e+11
(pid=75931) basinhopping step 10: f -2.08395e+11 trial_f -6.7196e+10 accepted 0  lowest_f -2.08395e+11
(pid=76478) basinhopping step 1: f 1.13051e+08 trial_f 2.16257e+08 accepted 0  lowest_f 1.13051e+08
(pid=76478) basinhopping step 2: f 1.13051e+08 trial_f 2.76187e+11 accepted 0  lowest_f 1.13051e+08
(pid=76195) basinhopping step 6: f -1.11499e+12 trial_f 1.65358e+08 accepted 0  lowest_f -1.11499e+12
(pid=76194) basinhopping step 6: f -8.89422e+13 trial_f 6.58574e+08 accepted 0  lowest_f -8.89422e+13
(pid=76477) basinhopping step 1: f -2.67714e+08 trial_f 4.71749e+07 accepted 0  lowest_f -2.67714e+08
(pid=76631) basinhopping step 0: f -1.05292e+11
(pid=76478) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full

(pid=76813) basinhopping step 0: f -1.73908e+08
(pid=76813) basinhopping step 1: f -1.73908e+08 trial_f 6.38304e+07 accepted 0  lowest_f -1.73908e+08
(pid=76709) basinhopping step 5: f -3.66438e+13 trial_f 7.79506e+11 accepted 0  lowest_f -3.66438e+13
(pid=76813) basinhopping step 2: f -1.73908e+08 trial_f 6.41879e+07 accepted 0  lowest_f -1.73908e+08
(pid=75971) basinhopping step 10: f -2.64972e+11 trial_f -8.79753e+09 accepted 0  lowest_f -2.64972e+11
(pid=76710) warning: basinhopping: local minimization failure
(pid=76710) basinhopping step 6: f -1.09096e+12 trial_f -1.09096e+12 accepted 1  lowest_f -1.09096e+12
(pid=76710) found new global minimum on step 6 with function value -1.09096e+12
(pid=76812) basinhopping step 0: f -2.32699e+11
(pid=76477) basinhopping step 6: f -6.2877e+11 trial_f -2.12302e+09 accepted 0  lowest_f -6.2877e+11
(pid=76710) basinhopping step 7: f -1.09096e+12 trial_f 1.3838e+09 accepted 0  lowest_f -1.09096e+12
(pid=76813) /home/ats4i/anaconda3/lib/python3.7

(pid=76876) basinhopping step 2: f -8.39764e+11 trial_f -6.93372e+11 accepted 0  lowest_f -8.39764e+11
(pid=76812) basinhopping step 6: f -5.87502e+11 trial_f -2.33062e+11 accepted 0  lowest_f -5.87502e+11
(pid=76988) basinhopping step 4: f 7.88392e+07 trial_f 1.22475e+08 accepted 0  lowest_f 7.88392e+07
(pid=76940) basinhopping step 4: f -3.27677e+11 trial_f 1.46555e+09 accepted 0  lowest_f -3.27677e+11
(pid=76989) basinhopping step 3: f -2.67069e+11 trial_f -2.67069e+11 accepted 1  lowest_f -2.67069e+11
(pid=76989) found new global minimum on step 3 with function value -2.67069e+11
(pid=76940) basinhopping step 5: f -3.27677e+11 trial_f 1.42827e+09 accepted 0  lowest_f -3.27677e+11
(pid=76876) basinhopping step 3: f -8.39764e+11 trial_f 5.13031e+07 accepted 0  lowest_f -8.39764e+11
(pid=76877) basinhopping step 3: f -2.87805e+13 trial_f 7.54959e+08 accepted 0  lowest_f -2.87805e+13
(pid=76877) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWar

(pid=77148) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=77148)   warnings.warn(warning_msg, ODEintWarning)
(pid=77147) basinhopping step 1: f -3.47476e+13 trial_f 1.07938e+09 accepted 0  lowest_f -3.47476e+13
(pid=77373) warning: basinhopping: local minimization failure
(pid=77373) basinhopping step 4: f -6.31571e+11 trial_f -6.31571e+11 accepted 1  lowest_f -6.31571e+11
(pid=77373) found new global minimum on step 4 with function value -6.31571e+11
(pid=76940) basinhopping step 9: f -5.4721e+11 trial_f -3.26558e+11 accepted 0  lowest_f -5.4721e+11
(pid=76940) basinhopping step 10: f -5.4721e+11 trial_f 2.71345e+11 accepted 0  lowest_f -5.4721e+11
(pid=77372) basinhopping step 0: f -9.77509e+10
(pid=76988) warning: basinhopping: local minimization failure
(pid=76988) basinhopping step 10: f -6.42199e+11 trial_f 1.58

In [ ]:
for i in range(0,len(states)):    

    state=states[i]
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_Yabox.csv", sep=",", index=False)
    dfparam
    